# Sayansi ya Takwimu katika Wingu: Njia ya "Azure ML SDK"

## Utangulizi

Katika daftari hili, tutajifunza jinsi ya kutumia Azure ML SDK kufundisha, kupeleka, na kutumia modeli kupitia Azure ML.

Mahitaji ya awali:
1. Umeunda nafasi ya kazi ya Azure ML.
2. Umeweka [Seti ya Takwimu ya Moyo Kushindwa](https://www.kaggle.com/andrewmvd/heart-failure-clinical-data) kwenye Azure ML.
3. Umeweka daftari hili kwenye Azure ML Studio.

Hatua zinazofuata ni:

1. Unda Jaribio katika Nafasi ya Kazi iliyopo.
2. Unda klasta ya Kompyuta.
3. Pakia seti ya takwimu.
4. Sanidi AutoML kwa kutumia AutoMLConfig.
5. Endesha jaribio la AutoML.
6. Chunguza matokeo na pata modeli bora.
7. Sajili modeli bora.
8. Peleka modeli bora.
9. Tumia sehemu ya mwisho.

## Uingizaji maalum wa Azure Machine Learning SDK


In [ ]:
from azureml.core import Workspace, Experiment
from azureml.core.compute import AmlCompute
from azureml.train.automl import AutoMLConfig
from azureml.widgets import RunDetails
from azureml.core.model import InferenceConfig, Model
from azureml.core.webservice import AciWebservice

## Anzisha Eneo la Kazi  
Anzisha kitu cha eneo la kazi kutoka kwa usanidi uliohifadhiwa. Hakikisha faili ya usanidi ipo kwenye .\config.json  


In [ ]:
ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep = '\n')

## Unda jaribio la Azure ML

Wacha tuunde jaribio linaloitwa 'aml-experiment' katika workspace tuliyoianzisha hivi punde.


In [ ]:
experiment_name = 'aml-experiment'
experiment = Experiment(ws, experiment_name)
experiment

## Kuunda Klasta ya Kompyuta  
Utahitaji kuunda [lengo la kompyuta](https://docs.microsoft.com/azure/machine-learning/concept-azure-machine-learning-architecture#compute-target) kwa ajili ya uendeshaji wako wa AutoML.  


In [ ]:
aml_name = "heart-f-cluster"
try:
    aml_compute = AmlCompute(ws, aml_name)
    print('Found existing AML compute context.')
except:
    print('Creating new AML compute context.')
    aml_config = AmlCompute.provisioning_configuration(vm_size = "Standard_D2_v2", min_nodes=1, max_nodes=3)
    aml_compute = AmlCompute.create(ws, name = aml_name, provisioning_configuration = aml_config)
    aml_compute.wait_for_completion(show_output = True)

cts = ws.compute_targets
compute_target = cts[aml_name]

## Data
Hakikisha umeweka seti ya data kwenye Azure ML na kwamba ufunguo una jina sawa na seti ya data.


In [ ]:
key = 'heart-failure-records'
dataset = ws.datasets[key]
df = dataset.to_pandas_dataframe()
df.describe()

In [ ]:
automl_settings = {
    "experiment_timeout_minutes": 20,
    "max_concurrent_iterations": 3,
    "primary_metric" : 'AUC_weighted'
}

automl_config = AutoMLConfig(compute_target=compute_target,
                             task = "classification",
                             training_data=dataset,
                             label_column_name="DEATH_EVENT",
                             enable_early_stopping= True,
                             featurization= 'auto',
                             debug_log = "automl_errors.log",
                             **automl_settings
                            )

In [ ]:
remote_run = experiment.submit(automl_config)

In [ ]:
RunDetails(remote_run).show()

In [ ]:
best_run, fitted_model = remote_run.get_output()

In [ ]:
best_run.get_properties()

In [ ]:
model_name = best_run.properties['model_name']
script_file_name = 'inference/score.py'
best_run.download_file('outputs/scoring_file_v_1_0_0.py', 'inference/score.py')
description = "aml heart failure project sdk"
model = best_run.register_model(model_name = model_name,
                                description = description,
                                tags = None)

## Kusambaza Modeli Bora

Endesha msimbo ufuatao ili kusambaza modeli bora. Unaweza kuona hali ya usambazaji katika Azure ML portal. Hatua hii inaweza kuchukua dakika chache.


In [ ]:
inference_config = InferenceConfig(entry_script=script_file_name, environment=best_run.get_environment())

aciconfig = AciWebservice.deploy_configuration(cpu_cores = 1,
                                               memory_gb = 1,
                                               tags = {'type': "automl-heart-failure-prediction"},
                                               description = 'Sample service for AutoML Heart Failure Prediction')

aci_service_name = 'automl-hf-sdk'
aci_service = Model.deploy(ws, aci_service_name, [model], inference_config, aciconfig)
aci_service.wait_for_deployment(True)
print(aci_service.state)

## Tumia Endpoint
Unaweza kuongeza viingizo kwenye sampuli ya kiingizo ifuatayo.


In [ ]:
data = {
    "data":
    [
        {
            'age': "60",
            'anaemia': "false",
            'creatinine_phosphokinase': "500",
            'diabetes': "false",
            'ejection_fraction': "38",
            'high_blood_pressure': "false",
            'platelets': "260000",
            'serum_creatinine': "1.40",
            'serum_sodium': "137",
            'sex': "false",
            'smoking': "false",
            'time': "130",
        },
    ],
}

test_sample = str.encode(json.dumps(data))

In [ ]:
response = aci_service.run(input_data=test_sample)
response


---

**Kanusho**:  
Hati hii imetafsiriwa kwa kutumia huduma ya tafsiri ya AI [Co-op Translator](https://github.com/Azure/co-op-translator). Ingawa tunajitahidi kwa usahihi, tafadhali fahamu kuwa tafsiri za kiotomatiki zinaweza kuwa na makosa au kutokuwa sahihi. Hati ya asili katika lugha yake ya awali inapaswa kuzingatiwa kama chanzo cha mamlaka. Kwa taarifa muhimu, inashauriwa kutumia tafsiri ya kitaalamu ya binadamu. Hatutawajibika kwa maelewano mabaya au tafsiri zisizo sahihi zinazotokana na matumizi ya tafsiri hii.
